In [34]:
import pandas as pd
import numpy as np
import sklearn.metrics as metrics
from random import randint
from matplotlib import pyplot as plt

In [35]:
!pip freeze > requirements.txt

In [36]:
import datetime
from common import get_full_data
from ucimlrepo import fetch_ucirepo 
from df_encodings import label_encode

def generated(noise_proportion=0.1):
    def f(x,y): 
        xy = x*y
        return xy+np.cos(3*xy)/2-np.sin(2*y**2)/3
    def add_noise(y):
        random_ind = np.random.uniform(0,1,len(y))<noise_proportion
        y=np.copy(y)
        rnd_points = y[random_ind]
        y[random_ind]=rnd_points+np.random.uniform(-1,1,size=len(rnd_points))
        return y
    # xy = np.random.uniform(-2,2,(10000,2))
    xy = np.random.uniform(-2,2,(10000,2))
    
    target = f(xy[:,0],xy[:,1]).flatten()
    mat = xy
    X = pd.DataFrame(mat,columns=['x','y'])
    std = np.std(target)
    target += np.random.uniform(-std,std,len(target))/10
    target=add_noise(target)
    target = pd.Series(target.flatten(),name='f_xy')
    return X,target
# load data
def steel_strength():
    df = pd.read_csv("dataset/steel_strength.csv")
    # get dependent and independent features
    X=df.iloc[:,1:-3]
    y=df.iloc[:,-2]
    return get_full_data(X,y)

def renewable():
    df = pd.read_csv("dataset/Renewable.csv")
    time = df["Time"].apply(lambda x: datetime.datetime.fromisoformat(x))
    df=df.drop(columns=["Time"])
    df["month"] = time.apply(lambda t: t.month)
    df["day"] = time.apply(lambda t: t.day)
    df["hour"] = time.apply(lambda t: t.hour)
    df["minute"] = time.apply(lambda t: t.minute)
    return df.iloc[:,1:], df.iloc[:,0]

def covertype():
    dataset_id = 31
    # load dataset
    annealing = fetch_ucirepo(id=dataset_id) 
    
    # load pandas from it
    X : pd.DataFrame = annealing.data.features 
    y = annealing.data.targets 
    # create concat dataset
    df = pd.concat([X,y],axis=1)

    # replace class label with Elevation to do regression
    return df.drop(columns=['Elevation']),df['Elevation']
def bikes():
    dataset_id = 560
    # load dataset
    annealing = fetch_ucirepo(id=dataset_id) 
    
    # load pandas from it
    X : pd.DataFrame = annealing.data.features 
    y = annealing.data.targets 

    d = X['Date'].apply(lambda t: t.split('/'))
    X=X.drop(columns=["Date"])

    X['days'] = d.apply(lambda t:t[0])
    X['months'] = d.apply(lambda t:t[1])
    X['years'] = d.apply(lambda t:t[2])
    df = pd.concat([label_encode(X)[0],label_encode(y)[0]],axis=1)
    return df.drop(columns=['Rented Bike Count']),df['Rented Bike Count']

In [37]:
from xgboost import XGBRegressor
from sklearn.preprocessing import StandardScaler
X,y = bikes()

# for high-dimensional data use `gpu` for device if you have one
special_model = XGBRegressor(device='cpu')

scaler = StandardScaler()
X_norm = scaler.fit_transform(X.to_numpy())

In [38]:
from sklearn.model_selection import RandomizedSearchCV, train_test_split
from common import XGB_search_params

params = XGB_search_params()
state = randint(0,1000)
search = RandomizedSearchCV(
    special_model,
    params,
    n_iter=150,
    cv=5,
    random_state=state,
    n_jobs=-1
)

# amount of samples used for parameters search
search_space_samples=7000

if search_space_samples>=len(X):
    search_space_samples=len(X)-1

_,X_search,_,y_search = train_test_split(X,y,test_size=search_space_samples/len(X))

search.fit(X_search,y_search)
special_model=search.best_estimator_

In [39]:
# do repeated stratified k-fold cross-validation with classification report
from sklearn.model_selection import RepeatedKFold, cross_val_score
from common import cross_val_score_mean_std

cv = RepeatedKFold(n_splits=5, n_repeats=2, random_state=50)
r2_scoring = metrics.make_scorer(metrics.r2_score)
orig_data_score=cross_val_score(special_model,X,y,cv=cv,scoring=r2_scoring)

In [40]:
from sklearn.decomposition import PCA, KernelPCA as KPCA
from common import cross_val_score_mean_std
from kernel_pca_search import kernel_pca_scorer
from render import *

setup="3D"

if setup=="3D":
    # 3d setup
    render_shuffle = [0,1,5,2,3,4]
    dot_size=3
    n_components=5
    axis_names = ['d1','d2',y.name]
    plot_method = plot_3d_rgb
    axis_sizes = [None,None,(min(y),max(y))]
if setup=="2D":
    # 2d setup    
    render_shuffle = [0,4,1,2,3]
    dot_size=5
    n_components=4
    axis_names = ['d1',y.name]
    plot_method = plot_2d_rgb

max_render = 10000
def render_results(cleaned_data_score,scaler,X_clean,y_clean,y,title="clean data"):
    X_clean_small = pca.transform(scaler.transform(X_clean[:max_render]))
    to_render=np.concatenate([X_clean_small,y_clean[:max_render]],axis=1)
    removed_size = 1-len(y_clean)/len(y)
    print("removed ",removed_size)
    if removed_size==0:
        return
    print("r2 score on",title)
    cross_val_score_mean_std(cleaned_data_score,y.name)
    plot_method(to_render[:max_render,render_shuffle],title,axis_names, template='plotly_dark',dot_size=dot_size,axis_sizes=axis_sizes)


pca = KPCA(n_components=n_components,kernel='rbf',fit_inverse_transform=True)
# pca = PCA(n_components=n_components)
X_small = pca.fit_transform(X_norm[:max_render])
y_n = y.to_numpy()[:max_render,np.newaxis]
X_small=np.concatenate([X_small,y_n],axis=1)
# print(sum(pca.explained_variance_ratio_))
print("r2 score on original data")
cross_val_score_mean_std(orig_data_score,y.name)
plot_method(X_small[:,render_shuffle],"original data",axis_names, template='plotly_dark',dot_size=dot_size,axis_sizes=axis_sizes)
print("Dim reduction quality",kernel_pca_scorer(pca,X_norm))

r2 score on original data
-----------Rented Bike Count-----------
Mean  0.8986845399700044
Std  0.007009452085966782


Dim reduction quality 0.4986495380468122


In [41]:
# New method
from common import find_outliers
X_numpy = X.to_numpy()
y_numpy = y.to_numpy()

outliers_to_remove=0.1

outliers_mask, score = find_outliers(
    X_numpy,
    y_numpy,
    special_model,
    outliers_to_remove=outliers_to_remove,
    iterations=5,
    gamma=0.99,
    evaluate_loss=metrics.mean_squared_error,
    cv=5,
    repeats=3,
    plot=False
)
X_clean = X_numpy[~outliers_mask]
y_clean = y_numpy[~outliers_mask]

r2_scoring = metrics.make_scorer(metrics.r2_score)
cleaned_data_score=cross_val_score(special_model,X_clean,y_clean,cv=cv,scoring=r2_scoring)

X_clean = X_numpy[~outliers_mask]
y_clean = y_numpy[~outliers_mask][:,np.newaxis]
render_results(cleaned_data_score,scaler,X_clean,y_clean,y,"iterative filtering")

removed  0.09965753424657531
r2 score on iterative filtering
-----------Rented Bike Count-----------
Mean  0.9672702199982754
Std  0.0021346126512964995


In [42]:
# z-score method
from scipy import stats
data = pd.concat([X,y],axis=1)
z = np.abs(stats.zscore(data))
threshold = 2
data_clean = data[(z < threshold).all(axis=1)]
X_clean=data_clean.iloc[:,:-1]
y_clean=data_clean.iloc[:,-1]
y_clean = np.array(y_clean)[:,np.newaxis]

cleaned_z_score_data_score=cross_val_score(special_model,X_clean,y_clean,cv=cv,scoring=r2_scoring)
render_results(cleaned_z_score_data_score,scaler,X_clean,y_clean,y,"z-score filtering")

/home/vlad/Programs/Git/python-outliers-detector/venv/lib/python3.12/site-packages/sklearn/base.py:486: UserWarning:

X has feature names, but StandardScaler was fitted without feature names



removed  0.37511415525114156
r2 score on z-score filtering
-----------Rented Bike Count-----------
Mean  0.8505922942784713
Std  0.013174675974482904


In [43]:
from sklearn.ensemble import IsolationForest

clf = IsolationForest(random_state=50,contamination=outliers_to_remove)
outliers_pred=clf.fit_predict(data)

data_clean = data[outliers_pred==1]

X_clean=data_clean.iloc[:,:-1]
y_clean=data_clean.iloc[:,-1].to_numpy()[:,np.newaxis]

cleaned_isolation_forest_data_score=cross_val_score(special_model,X_clean,y_clean,cv=cv,scoring=r2_scoring)
render_results(cleaned_isolation_forest_data_score,scaler,X_clean,y_clean,y,"isolation forest filtering")


/home/vlad/Programs/Git/python-outliers-detector/venv/lib/python3.12/site-packages/sklearn/base.py:486: UserWarning:

X has feature names, but StandardScaler was fitted without feature names



removed  0.09999999999999998
r2 score on isolation forest filtering
-----------Rented Bike Count-----------
Mean  0.8886469816926601
Std  0.006284707126856698


In [44]:
def winsorize(data, low_percentile=5, high_percentile=95):
    low_cutoff = np.percentile(data, low_percentile)
    high_cutoff = np.percentile(data, high_percentile)
    data[data < low_cutoff] = low_cutoff
    data[data > high_cutoff] = high_cutoff
    return data

# Example usage
winsorized_data = winsorize(data,10,85)
X_clean=winsorized_data.iloc[:,:-1].to_numpy()
y_clean=winsorized_data.iloc[:,-1].to_numpy()[:,np.newaxis]
cleaned_winsorized_data_score=cross_val_score(special_model,X_clean,y_clean,cv=cv,scoring=r2_scoring)
render_results(cleaned_winsorized_data_score,scaler,X_clean,y_clean,y,"winsorized filtering")

removed  0.0


In [45]:
from sklearn.cluster import DBSCAN

def remove_outliers_dbscan(X, eps=0.3, min_samples=10):
    db = DBSCAN(eps=eps, min_samples=min_samples)
    y_db = db.fit_predict(X)
    return X[y_db != -1] 

dbscan_cleaned = remove_outliers_dbscan(data)
X_clean=dbscan_cleaned.iloc[:,:-1].to_numpy()
y_clean=dbscan_cleaned.iloc[:,-1].to_numpy()[:,np.newaxis]
cleaned_dbscan_data_score=cross_val_score(special_model,X_clean,y_clean,cv=cv,scoring=r2_scoring)
render_results(cleaned_dbscan_data_score,scaler,X_clean,y_clean,y,"dbscan filtering")

ValueError: Cannot have number of splits n_splits=5 greater than the number of samples: n_samples=0.

In [33]:
from sklearn.svm import OneClassSVM

def remove_outliers_svm(X):
    svm = OneClassSVM(nu=0.05, kernel="rbf", gamma=0.1)
    y_pred = svm.fit_predict(X)
    return X[y_pred == 1]  # Retain only inliers

svm_data_clean = remove_outliers_svm(data)
X_clean=svm_data_clean.iloc[:,:-1].to_numpy()
y_clean=svm_data_clean.iloc[:,-1].to_numpy()[:,np.newaxis]
cleaned_smv_score=cross_val_score(special_model,X_clean,y_clean,cv=cv,scoring=r2_scoring)
render_results(cleaned_smv_score,scaler,X_clean,y_clean,y,"svm filtering")

removed  0.05049999999999999
r2 score on svm filtering
-----------f_xy-----------
Mean  0.9561009192182283
Std  0.0015763404077241121
